### This Notebook is used to get the embeddings for question description column in  the dataset.

**Note :** The embeddings are already saved  in "pickle" format. There is no need to run this notebook again. This  notebook is included here for reference and completeness.


In [600]:
import numpy as np
import pandas as pd
import os
import re

In [601]:
dataset_folder = "/Users/poojajaiswal/OneDrive - Dalhousie University/MCS/CSCI 6612 Visual Analytics/Project/Dataset"

In [602]:
filenames = []
for x in list(range(10,18)):
    file = 'rajyasabha_questions_and_answers_20'+ str(x) + ".csv"
    filenames.append(file)

In [603]:
df1 = pd.read_csv('rajyasabha_questions_and_answers_2009.csv', engine='python')
df2 = pd.read_csv(filenames[0], engine='python')
df3 = pd.read_csv(filenames[1], engine='python')
df4 = pd.read_csv(filenames[2], engine='python')
df5 = pd.read_csv(filenames[3], engine='python')
df6 = pd.read_csv(filenames[4], engine='python')
df7 = pd.read_csv(filenames[5], engine='python')
df8 = pd.read_csv(filenames[6], engine='python')
df9 = pd.read_csv(filenames[7], engine='python')

In [3]:
# Combining all the files and sorting by datetime.

In [604]:
df = pd.concat([df1,df2,df3,df4,df5,df6,df7,df8,df9],ignore_index=True)
df.loc[:,'answer_date'] = pd.to_datetime(df.answer_date)
df = df.sort_values(by  = 'answer_date') 

In [400]:
# df.index = df.answer_date

In [621]:
df = df['question_description']

The question description is such that every question has 3 sub-question to reduce complexity we combine all of them

In [622]:
def remove_list_points(x:str):
    """Removing the alphabetical list points."""
    return re.sub('\([a-z]\)', '', x)

In [623]:
df = df.apply(remove_list_points)

In [624]:
df

83       whether it is a fact that some firms dealing i...
136       whether it is a fact that most of the Public ...
135       whether G-20 Finance Ministers meet was held ...
134       the details of pattern of increase in the rur...
133       whether Government has assessed the quantum o...
                               ...                        
85655     the details of the total investment made in t...
85656     whether the Central Government and CPSUs are ...
85657     whether it is a fact that the hybrid cars are...
85649     the effective role of National Monuments Auth...
85768     Whether it is a fact that the scrapping of Fi...
Name: question_description, Length: 89093, dtype: object

# Processing the question and answers

In [276]:
df.question_description[0]

' whether Government is aware that there is spurt in prices of gold in the country in the last few months;  if so, the reasons therefor;  whether the import policy of gold needs further changes in view of spurt in prices of gold; and  if so, the steps Government proposes to take to bring down the prices of gold in the country?'

In [326]:
import pandas as pd

#Data Preprocessing and Feature Engineering
import string
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer

# word2vec
from gensim.models import Word2Vec

In [625]:
df

83       whether it is a fact that some firms dealing i...
136       whether it is a fact that most of the Public ...
135       whether G-20 Finance Ministers meet was held ...
134       the details of pattern of increase in the rur...
133       whether Government has assessed the quantum o...
                               ...                        
85655     the details of the total investment made in t...
85656     whether the Central Government and CPSUs are ...
85657     whether it is a fact that the hybrid cars are...
85649     the effective role of National Monuments Auth...
85768     Whether it is a fact that the scrapping of Fi...
Name: question_description, Length: 89093, dtype: object

In [329]:

# def preprocess_texts(text: str) -> [str]:
#     """This function lowercases, removes digits, punctuations,stopwords, tokenizes and normalises the texts"""
#     lem = WordNetLemmatizer()
#     text = text.lower()
#     text = text.translate(str.maketrans('', '', string.punctuation+string.digits))
#     text_tokens = word_tokenize(text)
#     text_tokens = [lem.lemmatize(word) for word in text_tokens if word not in stopwords.words('english')]
#     return text_tokens

In [626]:
%%timeit
lem = WordNetLemmatizer()
punctuation_digits = str.maketrans('', '', string.punctuation+string.digits)
stopword = stopwords.words('english')
def tokenise(df):
    df = df.copy(deep=True)
    """This function lowercases, removes digits, punctuations,stopwords, tokenizes and normalises the texts"""
    lem = WordNetLemmatizer()
    punctuation_digits = str.maketrans('', '', string.punctuation+string.digits)
    stopword = stopwords.words('english')
    for index,question in df.iteritems():
        question = question.lower()
        question = question.translate(punctuation_digits)
        question_tokens = word_tokenize(question)
        question_tokens = [lem.lemmatize(word) for word in question_tokens if word not in stopword]
        df[index] = question_tokens
     
    return df
    
    

166 µs ± 14.5 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)


In [628]:
%%time
df_token = tokenise(df)p

CPU times: user 57.3 s, sys: 598 ms, total: 57.9 s
Wall time: 59.3 s


In [630]:
# model = Word2Vec(questions_tokens, min_count=1, size =50,iter =50)
model = Word2Vec(df_token,min_count=1)

In [646]:
model.wv.most_similar('agriculture')

[('agricultural', 0.780207097530365),
 ('farm', 0.6822717189788818),
 ('fishery', 0.6765708923339844),
 ('horticulture', 0.6712913513183594),
 ('farming', 0.644605815410614),
 ('dairy', 0.6073001623153687),
 ('msme', 0.5872455835342407),
 ('manufacturingconstruction', 0.569352388381958),
 ('msmes', 0.5652278661727905),
 ('husbandry', 0.5626657009124756)]

In [634]:
def vectorise(question:[str]) ->[float] :
    """This function will vectorise the words in the question and reduce the whole question by mean."""
    if len(question)>0 :
        question = model.wv[question]
        question = np.question(question,axis=0)
    else :
        question = np.zeros(100)
    
    return question

In [635]:
df_question_description_vectors = df_token.apply(vectorise)

In [661]:
from scipy.spatial import distance
def get_most_similar(question_vector : np.array , questions_vectors :[np.array]):
    """This function returns the indexes of the most similar question."""
    distances = [(index,distance.cosine(question_vector,value)) for index,value in questions_vectors.iteritems()]
    
    most_similar = sorted(distances,key = lambda x : x[1])

    return most_similar
    

In [723]:
df.loc[20]

' the details of central universities which have been given minority status, State-wise;  the criterion for granting minority status to universities;  the details of facilities given to those institutions/ universities which have been granted minority status;  whether Government will grant minority status to Jamia Millia Islamia; and  if so, by when and if not, the reasons thereof?'

In [725]:
df.loc[9120]

' the number of educational institutions in our country that have got minority status by the order of National Commission for Minority Educational Institutions (NCMEI);  the details thereof, State-wise and year-wise; and  whether any specific guidelines to determine minority status exist?'

### We tried two models for vectorising Word2vec and Doc2Vec. In the final version we decided to use Word2Vec for simplicity.

In [532]:
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument

common_texts

documents = [TaggedDocument(doc, [i]) for i, doc in enumerate(df_token)]

model_doc = Doc2Vec(documents, vector_size=10, window=4, min_count=1, workers=4)

In [540]:
model_doc.wv.most_similar('rupee')

[('penny', 0.9314305186271667),
 ('fivefold', 0.923876941204071),
 ('ì', 0.9166343808174133),
 ('mgfemmar', 0.9160035848617554),
 ('moreb', 0.9147072434425354),
 ('croreslno', 0.9075325727462769),
 ('pricemep', 0.9030519127845764),
 ('worth', 0.8997265100479126),
 ('tune', 0.8984656929969788),
 ('precariously', 0.8956177234649658)]

In [541]:
doc_vectors = model_doc.docvecs.vectors_docs

In [550]:
some = []
for index,distance in enumerate(model_doc.docvecs.distances(10)):
    some.append([index,distance])
                        



In [551]:
distances_doc = sorted(some,key = lambda x: x[1])

In [552]:
distances_doc

[[10, 5.9604645e-08],
 [2921, 0.05366552],
 [70901, 0.06565565],
 [28086, 0.06890398],
 [46591, 0.0692479],
 [21952, 0.07402754],
 [51068, 0.075647116],
 [42261, 0.07672405],
 [46508, 0.07836974],
 [84916, 0.07844335],
 [69185, 0.07894951],
 [57410, 0.08239162],
 [69306, 0.08454698],
 [40987, 0.0888651],
 [32291, 0.09041512],
 [39154, 0.091947556],
 [56918, 0.095781684],
 [53729, 0.096761644],
 [18828, 0.09681654],
 [24373, 0.10224205],
 [42935, 0.10268837],
 [37732, 0.10420871],
 [77299, 0.10522127],
 [20915, 0.10571176],
 [62704, 0.108275],
 [28228, 0.110565245],
 [54572, 0.11201918],
 [24507, 0.11236429],
 [54628, 0.11288309],
 [37710, 0.113081455],
 [32781, 0.11384201],
 [44024, 0.11794597],
 [34843, 0.1182856],
 [69222, 0.11880338],
 [31020, 0.11891967],
 [35775, 0.11919886],
 [1811, 0.11938661],
 [45475, 0.12110776],
 [6432, 0.12147987],
 [42819, 0.12218261],
 [87255, 0.12467843],
 [59860, 0.124813974],
 [53604, 0.1248427],
 [8682, 0.12576365],
 [70439, 0.12634242],
 [82338, 0.12

In [549]:
df.question_description[10]

'(a) the quantity of rice and vegetables being exported and their volume and value, product-wise; and (b) whether any trial of GM vegetables and their productions will have any adverse effect on the quantity of exports?'

In [554]:
df.question_description[70901]

'(a) what is the progress on declaring eco-sensitive areas (ESAs) in Western Ghats;(b) how many States have submitted their report on demarcating ESAs by physical verification;(c) what is the procedure to be followed by the State to hold public consultations before demarcating ESAs by physical verification;(d) how many public consultations were held in Maharashtra for demarcation of ESAs, village-wise; and(e) whether report of the State would be accepted, even if no public consultation is held and if so, the reasons therefor?'

In [199]:
questions_vectors = questions_tokens.apply(vectorise)

['whether', 'fact', 'firm', 'dealing', 'power', 'communication', 'infrastructure', 'sector', 'violated', 'external', 'commercial', 'borrowing', 'ecb', 'guideline', 'reserve', 'bank', 'india', 'rbi', 'last', 'two', 'year', 'detail', 'thereof', 'name', 'company', 'penalty', 'imposed', 'etc', 'rbi', 'whether', 'big', 'industrial', 'group', 'involved', 'violation', 'ecb', 'guideline', 'evolved', 'new', 'mechanism', 'strategy', 'byepass', 'pending', 'liability', 'approached', 'rbi', 'ecb', 'approval', 'group', 'subsidiary', 'company', 'step', 'government', 'taken', 'ensure', 'subsidiary', 'new', 'company', 'singleumbrella', 'group', 'circumvent', 'rbi', 'guideline', 'unless', 'pending', 'violation', 'resolved']
['whether', 'fact', 'public', 'sector', 'bank', 'failed', 'achieve', 'mandatory', 'per', 'cent', 'credit', 'agriculture', 'sector', 'detail', 'thereof', 'last', 'three', 'year', 'yearwise', 'bankwise', 'reason', 'non', 'achievement', 'disbursal', 'agriloan', 'public', 'sector', 'bank

['per', 'caput', 'income', 'pci', 'current', 'price', 'last', 'three', 'year', 'difference', 'pci', 'rural', 'urban', 'india', 'comparative', 'price', 'rise', 'household', 'use', 'commodity', 'comparison', 'percentage', 'rise', 'pci', 'nation', 'whether', 'increase', 'pci', 'illusory']
['fund', 'given', 'state', 'central', 'fund', 'basis', 'performance', 'panchayat', 'empowerment', 'accountability', 'incentive', 'schemepeais', 'eleventh', 'five', 'year', 'plan', 'name', 'state', 'reason', 'giving', 'le', 'fund', 'state', 'scheme']
['whether', 'number', 'proposal', 'submitted', 'state', 'government', 'karnataka', 'swaranjayanti', 'grameen', 'swarozgar', 'yojana', 'sgsy', 'strengthening', 'district', 'rural', 'development', 'agency', 'drda', 'pradhan', 'mantri', 'grameen', 'swarojgar', 'yojana', 'pmgsy', 'seeking', 'central', 'assistance', 'present', 'pending', 'ministry', 'detail', 'proposal', 'likely', 'cleared']
['whether', 'world', 'bank', 'proposed', 'provide', 'financial', 'assista

['whether', 'fact', 'disruption', 'flight', 'operation', 'fog', 'become', 'annual', 'feature', 'winter', 'despite', 'installation', 'modern', 'communication', 'navigational', 'system', 'whether', 'also', 'fact', 'passenger', 'general', 'complaint', 'lack', 'timely', 'correct', 'informationmistreatment', 'lack', 'arrangement', 'airline', 'whether', 'government', 'looked', 'hardship', 'faced', 'passenger', 'whether', 'government', 'issued', 'necessary', 'direction', 'airline', 'regarding', 'standard', 'public', 'facility', 'information', 'system', 'detail', 'thereof']
['whether', 'long', 'term', 'settlement', 'employee', 'banking', 'sector', 'including', 'gramin', 'bank', 'finalized', 'detail', 'thereof', 'whether', 'fact', 'banking', 'sector', 'certain', 'percentage', 'increased', 'salary', 'bank', 'employee', 'deducted', 'pension', 'fund', 'however', 'deduction', 'salary', 'would', 'effective', 'gramin', 'bank', 'employee', 'officer', 'officer', 'employee', 'state', 'bank', 'india', 's

['whether', 'proposal', 'orissa', 'government', 'pending', 'central', 'government', 'setting', 'hospital', 'dispensary', 'employee', 'state', 'insurance', 'corporation', 'esic', 'detail', 'thereof', 'whether', 'policy', 'related', 'decision', 'setting', 'medical', 'college', 'state', 'esic', 'taken', 'place', 'set', 'construction', 'work', 'building', 'started', 'whether', 'government', 'take', 'step', 'regard', 'setting', 'dental', 'college', 'angul', 'central', 'orissa', 'corporation']
['whether', 'government', 'rajasthan', 'submitted', 'proposal', 'government', 'india', 'declaration', 'new', 'national', 'highway', 'detail', 'thereof', 'national', 'highway', 'likely', 'declared', 'whether', 'government', 'rajasthan', 'also', 'requested', 'centre', 'construction', 'ring', 'road', 'johdpur', 'city', 'nhdp', 'phasevii', 'construction', 'ring', 'road', 'jodhpur', 'city', 'likely', 'commenced']
['whether', 'fact', 'government', 'decided', 'select', 'major', 'capital', 'investor', 'place',

['rise', 'agricultural', 'input', 'cost', 'effect', 'farmer', 'last', 'three', 'year', 'whether', 'interest', 'farmer', 'agriculture', 'sector', 'declining', 'result', 'thereof', 'detail', 'thereof', 'step', 'taken', 'government', 'check', 'rise', 'input', 'cost', 'illeffects', 'farmer']
['whether', 'two', 'lakh', 'farmer', 'committed', 'suicide', 'country', 'far', 'detail', 'thereof', 'whether', 'government', 'contemplating', 'announce', 'new', 'farmer', 'friendly', 'agricultural', 'policy', 'detail', 'thereof', 'reason', 'ignoring', 'plight', 'farmer', 'large', 'scale', 'suicide']
['whether', 'order', 'tackle', 'food', 'crisis', 'country', 'government', 'taking', 'step', 'encourage', 'farmer', 'cultivate', 'coarse', 'grain', 'measurealternative', 'detail', 'thereof', 'whether', 'government', 'work', 'plan', 'enhance', 'utility', 'using', 'new', 'technology', 'hybrid', 'seed', 'reason', 'therefor']
['whether', 'government', 'proposes', 'promote', 'contract', 'farming', 'country', 'det

...

['whether', 'government', 'attention', 'drawn', 'news', 'item', 'appeared', 'english', 'daily', 'dated', 'october', 'government', 'plan', 'regulate', 'multistate', 'body', 'like', 'bcci', 'government', 'reaction', 'thereto', 'whether', 'government', 'proposes', 'bring', 'legislation', 'ensure', 'transparency', 'accountability', 'various', 'ngo', 'including', 'management', 'trust', 'various', 'religious', 'sport', 'organisation', 'viz', 'iskcon', 'bcci', 'etc', 'legislation', 'introduced', 'parliament', 'reason', 'therefor', 'remedial', 'step', 'government', 'proposes', 'take', 'ensure', 'transparency', 'accountability', 'organisation']
['statewise', 'number', 'ip', 'officer', 'placed', 'suspension', 'chargesheeted', 'date', 'statewise', 'detail', 'case', 'central', 'government', 'intervenedduring', 'last', 'three', 'year', 'statewise', 'detail', 'case', 'central', 'government', 'proposes', 'intervene', 'whether', 'fact', 'home', 'minister', 'stated', 'delinquent', 'ip', 'officer', 'guj

['whether', 'hoarding', 'blackmarketing', 'essential', 'commodity', 'one', 'reason', 'rise', 'price', 'detail', 'measure', 'taken', 'check', 'hoarder', 'blackmarketers', 'many', 'hoarder', 'blackmarketers', 'arrested', 'prosecuted', 'convicted', 'till', 'date', 'state', 'union', 'territorywise']
['whether', 'government', 'set', 'panel', 'prepare', 'draft', 'national', 'corporate', 'governance', 'policy', 'detail', 'recommendation', 'made', 'panel', 'whether', 'government', 'since', 'examined', 'recommendation', 'national', 'policy', 'corporate', 'governance', 'likely', 'finalised']
['whether', 'department', 'related', 'parliamentary', 'standing', 'committee', 'finance', 'recommended', 'reopening', 'investor', 'helpline', 'project', 'whether', 'government', 'accepted', 'recommendation', 'committee', 'likely', 'reopened']
['whether', 'government', 'proposes', 'make', 'company', 'answerable', 'towards', 'corporate', 'social', 'responsibility', 'make', 'mandatory', 'company', 'detail', 're

['dr', 'gyan', 'prakash', 'pilania', 'minister', 'labour', 'employment', 'pleased', 'statewhether', 'government', 'launched', 'rashtriya', 'swasthya', 'bima', 'yojana', 'bpl', 'family', 'unit', 'five', 'unorganized', 'sector', 'october', 'many', 'family', 'eligible', 'insurance', 'cover', 'andhow', 'many', 'covered']
['shri', 'prakash', 'javadekarwill', 'minister', 'labour', 'employment', 'pleased', 'statewhether', 'central', 'government', 'formulated', 'welfare', 'scheme', 'different', 'section', 'unorganized', 'sector', 'worker', 'regarding', 'life', 'disability', 'cover', 'health', 'maternity', 'benefit', 'old', 'age', 'protection', 'benefit', 'unorganised', 'labour', 'social', 'security', 'act', 'detail', 'thereof', 'andthe', 'statewise', 'detail', 'money', 'allocated', 'state', 'purpose', 'much', 'work', 'done']
['shrimati', 'ratna', 'bai', 'minister', 'labour', 'employment', 'pleased', 'statewhether', 'least', 'indian', 'multinational', 'company', 'managing', 'provident', 'fund',

['government', 'indiaministry', 'earth', 'sciencesrajya', 'sabhaunstarred', 'question', 'answered', 'monday', 'march', 'reservation', 'promotion', 'shri', 'ambeth', 'rajan', 'minister', 'earth', 'science', 'pleased', 'state', 'whether', 'reservation', 'promotion', 'strictly', 'followed', 'implemented', 'ministry', 'per', 'provision', 'made', 'constitution', 'th', 'amendment', 'detail', 'promotion', 'made', 'last', 'five', 'year', 'category', 'reason', 'therefor', 'would', 'completedanswerminister', 'state', 'ministry', 'planning', 'minister', 'state', 'ministry', 'science', 'technology', 'minister', 'state', 'ministry', 'earth', 'sciencesdr', 'ashwani', 'kumar']
['whether', 'fact', 'proposal', 'restoration', 'cycle', 'retirement', 'member', 'legislative', 'council', 'local', 'authoritiesconstituencies', 'every', 'two', 'year', 'karnataka', 'government', 'pending', 'central', 'government', 'decade', 'detail', 'thereof', 'reason', 'inordinate', 'pendency', 'proposal', 'central', 'governm

ValueError: need at least one array to concatenate

In [770]:
embed = pd.DataFrame({
    'index' : df.index,
    'question': df,
    'vector' : df_question_description_vectors
    
})

Saving the embedding for later use in visualization.

In [776]:
import pickle
with open('embed_word2vec.pickle', 'wb') as f:
    pickle.dump(embed, f)